# Setup et imports

In [56]:
#!pip install contextily
import geopandas as gpd
import contextily as ctx
import matplotlib.pyplot as plt
import folium
import pandas as pd
import urllib3
from zipfile import ZipFile
import requests
import osmnx as ox
import networkx as nx

%matplotlib inline

# Utilisation de la bibliothèque OSMnx, qui utilise l'API Overpass

## Scrapping des données 
La bibliothèque donne beaucoup de possibilités de récuper les données, on peut le faire depuis une adresse, des coordonnées, la "désignation" d'un lieu. c'est cette dernière qu'on utilise car le lieu en question est suffisamment connu...

On récupère les données sous le format de la libary networkx, on peut le [convertir en GeoDataFrame](https://osmnx.readthedocs.io/en/stable/osmnx.html#osmnx.utils_graph.graph_from_gdfs) au besoin

### Réseau piéton au tour de la tour Eiffeil

In [58]:
#récupération des données piétons
tour_eiffel = "Tour Eiffel, Paris, Ile-de-France, France" #2.29394, 48.857551
g_eiffel = ox.graph_from_place(tour_eiffel,
    buffer_dist=1000,
    network_type="walk",
    retain_all=True,
    truncate_by_edge=True) #distance sur le réseau piéton, on peut mettre from address, from bbox, from a point
    # pour plus d'information : https://osmnx.readthedocs.io/en/stable/osmnx.html#osmnx.graph.graph_from_place

c:\Users\leopo\anaconda3\lib\site-packages\geopandas\array.py:524: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  return GeometryArray(vectorized.representative_point(self.data), crs=self.crs)
c:\Users\leopo\anaconda3\lib\site-packages\geopandas\array.py:524: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  return GeometryArray(vectorized.representative_point(self.data), crs=self.crs)
c:\Users\leopo\anaconda3\lib\site-packages\geopandas\array.py:524: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  return GeometryArray(vectorized.representative_point(self.data), crs=self.crs)


### Carte du réseau piéton à moins d'un kilomètre de la tour Eiffel

In [59]:
#carte interactive
# voir : https://osmnx.readthedocs.io/en/stable/osmnx.html#osmnx.folium.plot_graph_folium 
map_eiffel = ox.plot_graph_folium(g_eiffel, node_size=0, edge_color="#FFFF5C", edge_linewidth=0.25,tiles="OpenStreetMap")
map_eiffel

## Données des points of interests (catégorie plus général : geometries)

### Récupération des données pour les poi de loisirs

In [52]:
tags = {"leisure": True}
gdf_pois_eiffel = ox.geometries_from_place(tour_eiffel, tags, buffer_dist=1000)
gdf_pois_eiffel["center"]=gdf_pois_eiffel.centroid
#chaque ligne peut être soit un polygone (par exemple pour le champ de Mars), soit un point comme un restaurant : on calcul le centre pour avoir une référence unique
gdf_pois_eiffel.head()
#On récupère directement un geodataframe cette fois ci

c:\Users\leopo\anaconda3\lib\site-packages\geopandas\array.py:524: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  return GeometryArray(vectorized.representative_point(self.data), crs=self.crs)
c:\Users\leopo\anaconda3\lib\site-packages\geopandas\array.py:524: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  return GeometryArray(vectorized.representative_point(self.data), crs=self.crs)
C:\Users\leopo\AppData\Local\Temp\ipykernel_4192\807790284.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf_pois_eiffel["center"]=gdf_pois_eiffel.centroid


addr:housenumber                  geometry source  \
element_type osmid                                                          
node         1215364980              NaN  POINT (2.29061 48.85575)    NaN   
             1299471298              NaN  POINT (2.30078 48.85545)    NaN   
             2347279483              NaN  POINT (2.30009 48.85387)    NaN   
             2463833424              NaN  POINT (2.28314 48.85551)    NaN   
             2463876727              NaN  POINT (2.29598 48.85134)    NaN   

                        barrier        leisure                    name  \
element_type osmid                                                       
node         1215364980     NaN  sports_centre  Piscine Émile Anthoine   
             1299471298     NaN     playground                     NaN   
             2347279483     NaN     playground                     NaN   
             2463833424     NaN     playground                     NaN   
             2463876727     NaN     playground                     NaN   

                            sport  \
element_type osmid                  
node         1215364980  swimming   
             1299471298       NaN   
             2347279483       NaN   
             2463833424       NaN   
             2463876727       NaN   

                                                                   website  \
element_type osmid                                                           
node         1215364980  http://piscine.equipement.paris.fr/Piscine_Emi...   
             1299471298                                                NaN   
             2347279483                                                NaN   
             2463833424                                                NaN   
             2463876727                                                NaN   

                        wheelchair addr:street  ... type area lanes length  \
element_type osmid                              ...                          
node         1215364980        yes         NaN  ...  NaN  NaN   NaN    NaN   
             1299471298        NaN         NaN  ...  NaN  NaN   NaN    NaN   
             2347279483        NaN         NaN  ...  NaN  NaN   NaN    NaN   
             2463833424        NaN         NaN  ...  NaN  NaN   NaN    NaN   
             2463876727    limited         NaN  ...  NaN  NaN   NaN    NaN   

                        length_unit covered description:fr  \
element_type osmid                                           
node         1215364980         NaN     NaN            NaN   
             1299471298         NaN     NaN            NaN   
             2347279483         NaN     NaN            NaN   
             2463833424         NaN     NaN            NaN   
             2463876727         NaN     NaN            NaN   

                        note:opendata:surface_to weight  \
element_type osmid                                        
node         1215364980                      NaN    NaN   
             1299471298                      NaN    NaN   
             2347279483                      NaN    NaN   
             2463833424                      NaN    NaN   
             2463876727                      NaN    NaN   

                                           center  
element_type osmid                                 
node         1215364980  POINT (2.29061 48.85575)  
             1299471298  POINT (2.30078 48.85545)  
             2347279483  POINT (2.30009 48.85387)  
             2463833424  POINT (2.28314 48.85551)  
             2463876727  POINT (2.29598 48.85134)  

[5 rows x 93 columns]

### Carte interactive des points d'intérêt de loisirs à moins d'un kilomètre à pieds de la Tour Eiffel

In [54]:
"""
It is the classical folium method : you create a list with geometry point values (here gdf_pois_eiffel.center) and fir each 
coordinates, you add a marker. 
"""
tour_eiffel_coord = [48.857551, 2.29394]
map = folium.Map(location=tour_eiffel_coord, tiles="OpenStreetMap", zoom_start=14)

for poi in gdf_pois_eiffel.iterrows():
    # Place the markers with the popup labels and data
    x , y = (poi[1]['center'].x, poi[1]['center'].y)
    map.add_child(
        folium.Marker(
            location=[y,x],
            popup=
                 "Name: " + str(poi[1]['name']) + "<br>" #here to add name 
                + "type: " + str(poi[1]['leisure']) + "<br>" #type 
                + "Coordinates: " + str(y)+', '+str(x)
            ,
        
            icon=folium.Icon(color="blue"),
        )
    )


In [55]:
map

# Utilisation des données de geofabrik

In [ ]:
# Téléchargement :
# https://download.geofabrik.de/europe/france/ile-de-france.html
data_folder = "./data/"
zipname = "Ile-de-France-Geofabrik-free"
geofabrik_idf_shp_link = "https://download.geofabrik.de/europe/france/ile-de-france-latest-free.shp.zip"
r = requests.get(geofabrik_idf_shp_link)

open(data_folder+zipname+".zip",'wb').write(r.content)

In [ ]:
# unzip des données en provenance de :
geofabrik_folder = data_folder+zipname+"/"
datafile_name = 'gis_osm_pois_a_free_1.shp'
dataextensions_unzip = ['.shp','.shx','.cpg','.dbf','.prj']
with ZipFile(data_folder+zipname+".zip") as myzip:
    for ext in dataextensions_unzip :
        myzip.extract(datafile_name[:-4]+ext, path = geofabrik_folder)

In [21]:
# ouverture des données
df_pois = gpd.read_file(geofabrik_folder+datafile_name)

# note : pois stands for points of interests

In [22]:
"""
I Only keep leisure and some shops and markets (see documentation : https://download.geofabrik.de/osm-data-in-gis-formats-free.pdf) 
"""

df_pois  = df_pois[(df_pois["code"] >= 2201) 
                   & (df_pois["code"] <= 2706)]

In [23]:

df_pois = df_pois.reset_index(drop = True) #I restart index  

In [24]:
df_pois 

osm_id  code   fclass                    name  \
0         4083189  2204     park           Parc de Bercy   
1         4208595  2204     park           Champ de Mars   
2         4221369  2204     park      Jardin des Plantes   
3         4263203  2204     park  Jardin du Palais Royal   
4         4410586  2204     park                    None   
...           ...   ...      ...                     ...   
46023  1112119036  2421  shelter                    None   
46024  1112121750  2421  shelter                    None   
46025  1112127658  2421  shelter                    None   
46026  1112127661  2421  shelter                    None   
46027  1112130356  2421  shelter                    None   

                                                geometry  
0      POLYGON ((2.37807 48.83739, 2.37812 48.83741, ...  
1      POLYGON ((2.29187 48.85771, 2.29230 48.85801, ...  
2      POLYGON ((2.35510 48.84374, 2.35511 48.84375, ...  
3      POLYGON ((2.33672 48.86417, 2.33674 48.86422, ...  
4      POLYGON ((2.20680 48.87370, 2.20770 48.87409, ...  
...                                                  ...  
46023  POLYGON ((2.46203 48.81455, 2.46204 48.81456, ...  
46024  POLYGON ((2.41404 48.82155, 2.41410 48.82157, ...  
46025  POLYGON ((2.41030 48.82361, 2.41032 48.82362, ...  
46026  POLYGON ((2.40987 48.82409, 2.40989 48.82410, ...  
46027  POLYGON ((2.45191 48.84708, 2.45192 48.84711, ...  

[46028 rows x 5 columns]

In [25]:
"""
I use folium to create an interative map centered in Eiffel Tower
"""


map = folium.Map(location=[48.857551, 2.29394], tiles="OpenStreetMap", zoom_start=14)
map

In [26]:
"""
I use gpd.centroid to have polygon centers (more easy to manipulate) 
"""
# geometry (active) column
df_pois = df_pois.to_crs(epsg=4326)
df_pois['center'] = df_pois.centroid
# Centroid column
df_pois["center"] = df_pois['center'].to_crs(epsg=4326)

df_pois.head()

C:\Users\leopo\AppData\Local\Temp\ipykernel_19944\2415629637.py:6: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  df_pois['center'] = df_pois.centroid


osm_id  code fclass                    name  \
0  4083189  2204   park           Parc de Bercy   
1  4208595  2204   park           Champ de Mars   
2  4221369  2204   park      Jardin des Plantes   
3  4263203  2204   park  Jardin du Palais Royal   
4  4410586  2204   park                    None   

                                            geometry                    center  
0  POLYGON ((2.37807 48.83739, 2.37812 48.83741, ...  POINT (2.38212 48.83549)  
1  POLYGON ((2.29187 48.85771, 2.29230 48.85801, ...  POINT (2.29792 48.85605)  
2  POLYGON ((2.35510 48.84374, 2.35511 48.84375, ...  POINT (2.35926 48.84334)  
3  POLYGON ((2.33672 48.86417, 2.33674 48.86422, ...  POINT (2.33781 48.86501)  
4  POLYGON ((2.20680 48.87370, 2.20770 48.87409, ...  POINT (2.20915 48.87240)

In [27]:
"""
I filter a zone near Eiffel Tower. 
"""

gdf_pois = pd.concat([df_pois, df_pois.bounds], axis=1) #I use gpd bounds to have coordonnees in two columns and not only in Point(x,y) 

gdf_pois_eiffel = gdf_pois[(gdf_pois["minx"] >= 2.287592 ) &
        (gdf_pois["minx"] <= 2.314801) &
         (gdf_pois["miny"] >= 48.847194) &
        (gdf_pois["miny"] <= 48.866217)]

gdf_pois_eiffel = gdf_pois_eiffel.reset_index(drop = True) #reset index. 

In [28]:
"""
It is the classical folium method : you create a list with geometry point values (here gdf_pois_eiffel.center) and fir each 
coordinates, you add a marker. 
"""

geo_df_list = [[point.xy[1][0], point.xy[0][0]] for point in gdf_pois_eiffel.center] 


i = 0
for coordinates in geo_df_list:
    # Place the markers with the popup labels and data
    map.add_child(
        folium.Marker(
            location=coordinates,
            popup=
                 "Name: " + str(gdf_pois_eiffel.name[i]) + "<br>" #here to add name 
                + "type: " + str(gdf_pois_eiffel.fclass[i]) + "<br>" #type 
                + "Coordinates: " + str(geo_df_list[i])
            ,
        
            icon=folium.Icon(color="blue"),
        )
    )
    i = i + 1

In [29]:
map